In [215]:
import pandas as pd
import pingouin as pg

from scipy.stats import bartlett, levene

---

Reading and preprocessing data

In [216]:
DataWhr2024 = pd.read_csv("DataWhr2024.csv")
UnM49 = pd.read_csv("UnM49.csv", sep=';')

In [217]:
DataWhr2024.loc[DataWhr2024["Country name"].str.startswith("Hong"), "Country name"] = "Hong Kong"
DataWhr2024.loc[DataWhr2024["Country name"].str.startswith("Somaliland"), "Country name"] = "Somaliland"
DataWhr2024.loc[DataWhr2024["Country name"].str.startswith("Taiwan"), "Country name"] = "Taiwan"

In [218]:
UnM49 = UnM49[['Country or Area', 'Sub-region Name', 'Region Name']]
UnM49 = UnM49.rename({'Country or Area':'Country name', 'Sub-region Name':'Subregion', 'Region Name':'Continent'}, axis=1)

In [219]:
UnM49.loc[97, "Country name"] = "Bolivia"
UnM49.loc[33, "Country name"] = "Congo (Brazzaville)"
UnM49.loc[34, "Country name"] = "Congo (Kinshasa)"
UnM49.loc[124, "Country name"] = "Hong Kong"
UnM49.loc[125, "Country name"] = "Macao"
UnM49.loc[126, "Country name"] = "North Korea"
UnM49.loc[145, "Country name"] = "Iran"
UnM49.loc[46, "Country name"] = "Ivory Coast"
UnM49.loc[133, "Country name"] = "Laos"
UnM49.loc[129, "Country name"] = "South Korea"
UnM49.loc[173, "Country name"] = "Moldova"
UnM49.loc[217, "Country name"] = "Netherlands"
UnM49.loc[175, "Country name"] = "Russia"
UnM49.loc[164, "Country name"] = "Syria"
UnM49.loc[26, "Country name"] = "Tanzania"
UnM49.loc[116, "Country name"] = "United States"
UnM49.loc[193, "Country name"] = "United Kingdom"
UnM49.loc[111, "Country name"] = "Venezuela"
UnM49.loc[140, "Country name"] = "Vietnam"

In [220]:
_ = pd.DataFrame(
    {
        "Country name": ["Kosovo", "Somaliland", "Taiwan"],
        "Subregion": ["Southern Europe", "Sub-Saharan Africa", "Eastern Asia"],
        "Continent": ["Europe", "Africa", "Asia"],
    }
)

UnM49 = pd.concat([UnM49, _], axis=0)
UnM49 = UnM49.reset_index(drop=True)

Merging the datasets

In [221]:
# Data
Dat = pd.merge(DataWhr2024, UnM49)

# Data of 2023
Dat2023 = Dat[Dat['year'] == 2023]
Dat2023 = Dat2023.reset_index(drop=True)

**Question 1**

In [222]:
# Step 1: Southeast Asia Mean (μSE) and Hypothesis Testing
Dat2023SEA = Dat2023[Dat2023['Subregion'] == 'South-eastern Asia']['Life Ladder']

mu_se = Dat2023SEA.mean()

t_test_result = pg.ttest(Dat2023SEA, 5.7)

print(f"μSE: {mu_se:.3f}\n")
print(f"One-sample t-test result:\n{t_test_result}\n")

μSE: 5.678

One-sample t-test result:
               T  dof alternative     p-val         CI95%   cohen-d   BF10  \
T-test -0.075657    8   two-sided  0.941549  [5.02, 6.34]  0.025219  0.322   

           power  
T-test  0.050515  



**Question 2**

In [223]:
# Step 2: Variance (σ²SE, σ²LA) and Hypothesis Testing
Dat2023LA = Dat2023[Dat2023['Subregion'] == 'Latin America and the Caribbean']['Life Ladder']

sigma2_se = Dat2023SEA.var(ddof=1)
sigma2_la = Dat2023LA.var(ddof=1)

f_test_result = pg.homoscedasticity([Dat2023SEA.values, Dat2023LA.values], method='levene')

print(f"σ²SE: {sigma2_se:.3f}, σ²LA: {sigma2_la:.3f}\n")
print(f"Levene's test result:\n{f_test_result}\n")


σ²SE: 0.731, σ²LA: 0.194

Levene's test result:
               W      pval  equal_var
levene  3.141025  0.088534       True



**Question 3**

In [224]:
# Step 3: Mean (μLA) and Hypothesis Testing
mu_LA = Dat2023LA.values.mean()
t_test_ind_result = pg.ttest(Dat2023SEA, Dat2023LA)

print(f"μLA: {mu_LA:.3f}")
print(f"Two-sample t-test result:\n{t_test_ind_result}\n")

μLA: 6.297
Two-sample t-test result:
               T        dof alternative     p-val          CI95%   cohen-d  \
T-test -2.040107  10.186481   two-sided  0.068122  [-1.29, 0.06]  1.022676   

         BF10     power  
T-test  1.597  0.672925  



In [225]:
Dat2023['Continent'].dropna().count()

np.int64(138)

**Question 4**

In [243]:
import pingouin as pg
import pandas as pd
import numpy as np
'''
# Define the mapping of sub-regions to continents
sub_region_to_continent = {
    'Southern Asia': 'Asia',
    'South-eastern Asia': 'Asia',
    'Eastern Asia': 'Asia',
    'Central Asia': 'Asia',
    'Southern Europe': 'Europe',
    'Western Europe': 'Europe',
    'Eastern Europe': 'Europe',
    'Northern Europe': 'Europe',
    'Latin America and the Caribbean': 'America',
    'Northern America': 'America',
    'Sub-Saharan Africa': 'Africa',
    'Northern Africa': 'Africa',
    'Australia and New Zealand': 'Oceania'
}

# Map the 'Subregion' values to continents
Dat2023['Continent'] = Dat2023['Subregion'].map(sub_region_to_continent)
'''
# Drop rows with missing values in 'Continent' or 'Life Ladder'
anova_data = Dat2023[['Continent', 'Life Ladder']].dropna()

# Perform the ANOVA test
anova_result = pg.anova(data=anova_data, dv='Life Ladder', between='Continent', detailed=True)

# Print the ANOVA table
print("ANOVA Table:")
print(anova_result)

# Extract the relevant ANOVA results for sum of squares (SS)
ss_between = anova_result['SS'].iloc[0]  # Sum of Squares between
ss_within = anova_result['SS'].iloc[1]   # Sum of Squares within

# Extract the degrees of freedom (df) for between and within
df_between = anova_result['DF'].iloc[0]  # Degrees of freedom between
df_within = anova_result['DF'].iloc[1]   # Degrees of freedom within

# Extract the mean squares (MS) for between and within
ms_between = anova_result['MS'].iloc[0]  # Mean square between
ms_within = anova_result['MS'].iloc[1]   # Mean square within

# F-statistic
f_stat = ms_between / ms_within

# Post-hoc analysis if the null hypothesis is rejected
if anova_result['p-unc'].iloc[0] < 0.05:  # If H0 is rejected
    # Group statistics
    continent_means = anova_data.groupby('Continent')['Life Ladder'].mean()
    # Aggregating count, mean, and variance for each continent group
    DatGroup = anova_data.groupby("Continent")["Life Ladder"].agg(["count", "mean", "var"]).reset_index()

    # Extract the necessary columns for calculation
    count_values = DatGroup["count"]
    mean_values = DatGroup["mean"]
    var_values = DatGroup["var"]

    # Intercontinental mean (μ) calculation
    n_tot = len(anova_data)  # Total number of observations
    J = len(DatGroup)  # Number of continents/groups
    n_Bar = n_tot / J  # Average sample size per group

    mu = anova_data['Life Ladder'].mean()

    # Intercontinental Variance (τ²)
    tau_squared = (ms_between - ms_within) / n_Bar

    # Print results
    print("\nPost-Hoc Analysis:")
    print(f"Means by Continent:\n{continent_means.round(3)}")
    print(f"Intercontinental Mean (μ): {mu:.3f}")
    print(f"Intercontinental Variance (τ²): {tau_squared:.3f}")
else:
    print("\nGlobal Analysis:")
    global_mean = anova_data['Life Ladder'].mean()
    global_variance = anova_data['Life Ladder'].var(ddof=1)
    print(f"Global Mean (θ): {global_mean:.3f}")
    print(f"Global Variance (σ²): {global_variance:.3f}")


ANOVA Table:
      Source         SS   DF         MS          F         p-unc      np2
0  Continent  90.218922    4  22.554730  34.218881  1.271847e-19  0.50718
1     Within  87.664444  133   0.659131        NaN           NaN      NaN

Post-Hoc Analysis:
Means by Continent:
Continent
Africa      4.485
Americas    6.336
Asia        5.433
Europe      6.454
Oceania     7.001
Name: Life Ladder, dtype: float64
Intercontinental Mean (μ): 5.621
Intercontinental Variance (τ²): 0.793
